
# Data Exploration 

Imagine that we would like to build a ML model to predict the price of a listing based on lodaded data in raw area. 

Our primary goal at this stage is to conduct data exploration to identify and resolve potential issues with the data, such as invalid types, missing values, and anomalies. 

Please run <code>load_athens_airbnb_data</code> notebook to get dataset into <code>airbnb.raw</code> schema


## Load Listings Dataset

Let's load the Airbnb Athens listing dataset in.

In [0]:

raw_df = spark.read.table('airbnb.raw.listings')
display(raw_df)

listing_url scrape_id last_scraped source name description neighborhood_overview picture_url host_id host_url host_name host_since host_location host_about host_response_time host_response_rate host_acceptance_rate host_is_superhost host_thumbnail_url host_picture_url host_neighbourhood host_listings_count host_total_listings_count host_verifications host_has_profile_pic host_identity_verified neighbourhood neighbourhood_cleansed neighbourhood_group_cleansed latitude longitude property_type room_type accommodates bathrooms bathrooms_text bedrooms beds amenities price minimum_nights maximum_nights minimum_minimum_nights maximum_minimum_nights minimum_maximum_nights maximum_maximum_nights minimum_nights_avg_ntm maximum_nights_avg_ntm calendar_updated has_availability availability_30 availability_60 availability_90 availability_365 calendar_last_scraped number_of_reviews number_of_reviews_ltm number_of_reviews_l30d first_review last_review review_scores_rating review_scores_accuracy review_scores_cleanliness review_scores_checkin review_scores_communication review_scores_location review_scores_value license instant_bookable calculated_host_listings_count calculated_host_listings_count_entire_homes calculated_host_listings_count_private_rooms calculated_host_listings_count_shared_rooms reviews_per_month processing_datetime area https://www.airbnb.com/rooms/10595 20230921043851 2023-09-21 city scrape Condo in Athens · ★4.83 · 3 bedrooms · 5 beds · 2 baths The apartment is 3-bedroom apartment with 2-bathrooms on the 2nd floor. 1st bedroom - double bed with air-condition. 2nd bedroom - 2 single beds with air-condition 3rd bedroom - 2 single beds with air-condition Living room - 2 sofa beds with air-condition Fast free internet up to 100mbps Central heating on all day at around 21 c 10 λεπτά από το μετρό Πανόρμου και 100 μέτρα απο στάση λεωφορείου. Το διαμέρισμα είναι 100 μέτρα μακριά απο το Ξενοδοχείο President. The space The apartment is 3-bedroom apartment with 2-bathrooms on the 2nd floor. 1st bedroom - double bed with air-condition. 2nd bedroom - 2 single beds with air-condition 3rd bedroom - 2 single beds with air-condition Living room - 2 sofa beds with air-condition Fast free internet up to 100mbps Central heating on all day at around 21 c 10 minutes away from the Metro Blue line which is the direct line to come Ampelokipi district is nice multinational and safe area with excellent transportation system. Staying in Ampelokipi area you have the safety you need when you are in a foreign country. Everything you need for your vacations you can find it next to the apartment: Shops, Supermarkets, Restaurants, Bars, Coffee shops, Bakeries, Groceries, 24 hours kiosk, Pharmacies, Hair Salon, Banks, Travel Agents, Cinemas, summer cinemas and many more... Also every Saturday there is a Farmers market 2-3 minutes away from the apartment. Athens Classical Marathon route pass from the area. In the area you will also find Athens Concert Hall (Megaron Mousikis), National Sculpture Gallery, Badminton Theater (international shows), the biggest urban park in Athens, ministries, universities, embassies, hospitals and more… https://a0.muscache.com/pictures/f7e19a44-5afe-4558-8b5d-2f8186723721.jpg 37177 https://www.airbnb.com/users/show/37177 Emmanouil 2009-09-08 Athens, Greece Athens Quality Apartments is a company started back at 2007 and now we have 8 apartments. Our goal is to offer to travelers beautiful apartments with professional service only in good location and with all the necessary amenities.
 within an hour 100% 98% t https://a0.muscache.com/im/pictures/user/859c1eda-f858-414e-9984-165bd4575b3f.jpg?aki_policy=profile_small https://a0.muscache.com/im/pictures/user/859c1eda-f858-414e-9984-165bd4575b3f.jpg?aki_policy=profile_x_medium Ambelokipi 8.0 10.0 ['email', 'phone'] t t Athens, Attica, Greece ΑΜΠΕΛΟΚΗΠΟΙ null 37.98863 23.76527 Entire condo Entire home/apt 10 null 2 baths 3.0 5.0 ["Keypad", "Hair dryer", "High chair", "Hot water", "

Databricks data profile. Run in Databricks to view.

In [0]:
raw_df.columns




For the sake of simplicity, only keep certain columns from this dataset.

In [0]:
columns_to_keep = [
    'host_id','host_since','host_is_superhost','latitude','longitude','property_type','room_type','accommodates','bathrooms','bathrooms_text','bedrooms','beds','amenities','price','minimum_nights','maximum_nights', 'number_of_reviews','review_scores_rating','license','instant_bookable','reviews_per_month'
]

base_df = raw_df.select(columns_to_keep)
display(base_df)



 
## Fixing Data Types

Take a look at the schema above. You'll notice that the **`price`** field got picked up as string. For our task, we need it to be a numeric (double type) field. 

Let's fix that.

In [0]:
from pyspark.sql.functions import col, translate

fixed_price_df = base_df.withColumn("price", translate(col("price"), "$,", "").cast("double"))

display(fixed_price_df)




## Summary statistics

Two options:
* **`describe`**: count, mean, stddev, min, max
* **`summary`**: describe + interquartile range (IQR)

**Question:** When to use IQR/median over mean? Vice versa?

In [0]:
display(fixed_price_df.describe())

In [0]:
display(fixed_price_df.summary())


### Explore Dataset with Data Profile

The **Data Profile** feature in Databricks notebooks offers valuable insights and benefits for data analysis and exploration. By leveraging Data Profile, users gain a comprehensive overview of their **dataset's characteristics, statistics, and data quality metrics**. This feature enables data scientists and analysts to understand the data distribution, identify missing values, detect outliers, and explore descriptive statistics efficiently.

There are two ways of viewing Data Profiler. The first option is the UI.

- After using `display` function to show a data frame, click **+** icon next to the *Table* in the header. 
- Click **Data Profile**. 



This functionality is also available through the dbutils API in Python, Scala, and R, using the dbutils.data.summarize(df) command. We can also use **`dbutils.data.summarize(df)`** to display Data Profile UI.

Note that this features will profile the entire data set in the data frame or SQL query results, not just the portion displayed in the table

In [0]:
dbutils.data.summarize(fixed_price_df)




## Extreme values

Let's take a look at the *min* and *max* values of the **`price`** column.

In [0]:
display(fixed_price_df.select("price").describe())

In [0]:
display(fixed_price_df.select('price'))

There are some super-expensive listings, and it's up to theSubject Matter Experts to decide what to do with them.
Let's see first how many listings we can find where the *price* is extream.

In [0]:
fixed_price_df.filter(col("price") >= 10000).count()




We have 1 listing that has extream values and lets remove it.

In [0]:
pos_prices_df = fixed_price_df.filter(col("price") < 10000)




Let's take a look at the *min* and *max* values of the *minimum_nights* column:

In [0]:
display(pos_prices_df)

In [0]:
display(pos_prices_df.select("minimum_nights").describe())

In [0]:
display(pos_prices_df
        .groupBy("minimum_nights").count()
        .orderBy(col("count").desc(), col("minimum_nights"))
       )




A minimum stay of 90 days seems to be a reasonable limit here due to . Let's filter out those records where the *minimum_nights* is greater than 90.

In [0]:
min_nights_df = pos_prices_df.filter(col("minimum_nights") <= 90)

display(min_nights_df)



## Fix bathrooms

It seems like bathroom column contains null values and information regarding bathrooms counts contained in bathrooms_text column.

In [0]:
display(min_nights_df.select('bathrooms', 'bathrooms_text'))

In [0]:

from pyspark.sql.functions import element_at, split

# this code will fail because of anusual data points
# please uncoment and try to figure out hoe to fix this. 

bathrooms_df = min_nights_df


# bathrooms_df = (
#   bathrooms_df
#   .withColumn('bathrooms', element_at(split('bathrooms_text', ' '), 1).cast('double'))
#   .drop('bathrooms_text')
# )

# display(bathrooms_df)





## Fix boolean columns types 

There are two columns `host_is_superhost` and `instant_bookable` that potentially may be usefull, but they are encoded as 't' or 'f' values.
Lets change it to boolean type. 


In [0]:
boolean_df = (
  bathrooms_df
  .withColumn('instant_bookable', col('instant_bookable') == 't')
  .withColumn('host_is_superhost', col('host_is_superhost') == 't')
)



## Fix amenities

We can notice that `amenities` column contains a list of available items but it looks like string list which is not easy to work with. 
PySpark has a number of build-in methods to work with arrays: __array_*__
Lets convert amenities into propper aray of strings column.

In [0]:

from pyspark.sql.functions import explode, lower

amenities_df = boolean_df.withColumn('amenities', split(translate('amenities', '\\]\\[\\"', ''), ','))

display(
  amenities_df
  .select(explode('amenities'))
  .withColumn('item', lower('col'))
  .groupBy('item').count()
  .sort('count')
)



## Combine all above transformations


In [0]:
def prepare_athens_listings(raw_df):
  from pyspark.sql.functions import col, translate, element_at, split, to_date
  columns_to_keep = [
      'host_id','host_since','host_is_superhost','latitude','longitude','property_type','room_type','accommodates','bathrooms','bathrooms_text','bedrooms','beds','amenities','price','minimum_nights','maximum_nights', 'number_of_reviews','review_scores_rating','license','instant_bookable','reviews_per_month'
      # any other columns you may find useful for our future model? 
  ]
  df = raw_df.select(*columns_to_keep)


  # to do
  # add validation to identify any unusual data points and mark them as invalid. please add reason why those datapoints are invalid. 
  
  return df 

df = prepare_athens_listings(raw_df)
display(df)




## Handling Null Values

There are a lot of different ways to handle null values. Sometimes, null can actually be a key indicator of the thing you are trying to predict (e.g. if you don't fill in certain portions of a form, probability of it getting approved decreases).

Some ways to handle nulls:
* Drop any records that contain nulls
* Numeric:
  * Replace them with mean/median/zero/etc.
* Categorical:
  * Replace them with the mode
  * Create a special category for null
  
**If you do ANY imputation techniques for categorical/numerical features, you MUST include an additional field specifying that field was imputed.**

In [0]:
# to do: 
# Work in team and brainstorm the best way to visualize missing values in dataset 

In [0]:
# to do: 

# create a new schema called 'validatated' in airbnb catalog and save your validated listing dataset.